# Importing Packages

In [28]:
import requests
from dotenv import load_dotenv
import pandas as pd
from sqlalchemy import create_engine, types
import sqlalchemy
import itertools
import folium
import copy
import os
import branca.colormap as cm
import streamlit as st
from geopy.geocoders import Nominatim
from streamlit_folium import folium_static

# Load Environment Variables

In [29]:
# Load authentication data in .env file
load_dotenv()

True

# Get Categories Data

In [6]:
def get_categories():
    response = requests.get('https://developers.zomato.com/api/v2.1/categories', headers=HEADERS)
    if response.status_code != 200:
        raise Exception('Failed to get the data')
    else:
        return response.status_code, response.json()
    
def read_categories(json_data):
    data = {idx:row['categories'] for idx, row in enumerate(json_data['categories'])}
    return pd.DataFrame.from_dict(data, orient='index')

# Get Cities Data

In [7]:
def get_cities(list_cities):
    params = {'q' : ','.join(list_cities)}
    response = requests.get('https://developers.zomato.com/api/v2.1/cities', headers=HEADERS, params=params)
    if response.status_code != 200:
        raise Exception('Failed to get the data')
    else:
        return response.status_code, response.json()

def read_cities(json_data):
    data = {idx:row for idx, row in enumerate(json_data['location_suggestions'])}
    return pd.DataFrame.from_dict(data, orient='index')

# Get Collections Data

In [8]:
def get_collections(list_city_id):
    all_data = []
    for record in list_city_id:
        params = {'city_id' : record, 'count' : 1000}
        response = requests.get('https://developers.zomato.com/api/v2.1/collections', headers=HEADERS, params=params)
        if response.status_code != 200:
            print(response.status_code)
            print(response.text)
            raise Exception('Failed to get the data')
        else:
            all_data.append(response.json())
    return response.status_code, all_data


def read_collections(json_data, list_city_id): 
    data = dict()
    row = 0
    for i in range(len(list_city_id)):
        record = dict()
        for j in range(len(json_data[i]['collections'])):
            record.update({'city_id' : list_city_id[i]})
            record.update(json_data[i]['collections'][j]['collection'])
            data.update({row : record.copy()})
            row += 1
    return pd.DataFrame.from_dict(data, orient='index')

# Get Restaurant Data

In [9]:
def city_collection_generator(list_city_id, list_collection_id):
    for pair in itertools.product(list_city_id, list_collection_id):
        yield pair

def get_search(list_city_id, list_collection_id):
    all_data = []
    for entity_id, collection_id in city_collection_generator(list_city_id, list_collection_id):
        params = {'entity_type':'city', 'entity_id':entity_id, 'collection_id':collection_id, 'start':0}
        response = requests.get('https://developers.zomato.com/api/v2.1/search', headers=HEADERS, params=params)
        try:    
            results_found = response.json()['results_found']
        except:
            print(response.json())
            raise Exception
        while params['start'] <= results_found:
            print('city_id: ', entity_id, 'collection_id: ', collection_id)
            print('start: ', params['start'], 'results_found: ', response.json()['results_found'], 'api call made: ', len(all_data)+1)
            
            sub_data = response.json()['restaurants']
            for each_resto in sub_data:
                each_resto['restaurant']['collection_id'] = collection_id
            all_data.append(sub_data[:])
            params['start'] += 20
            response = requests.get('https://developers.zomato.com/api/v2.1/search', headers=HEADERS, params=params)
    return response.status_code, [resto for page in all_data for resto in page]

def read_search_restaurant_detail(json_data):
    all_data = dict()
    row = 0
    for item in json_data:
        record = dict()
        resto = copy.deepcopy(item)
        record.update({'collection_id' : resto['restaurant']['collection_id']})
        record.update({'res_id' : resto['restaurant']['R']['res_id']})
        record.update({'is_grocery_store' : resto['restaurant']['R']['is_grocery_store']})
        record.update({'delivery' : resto['restaurant']['R']['has_menu_status']['delivery']})
        record.update({'takeway' : resto['restaurant']['R']['has_menu_status']['takeaway']})
        del resto['restaurant']['R']
        del resto['restaurant']['location']
        del resto['restaurant']['user_rating']
        del resto['restaurant']['all_reviews']
        record.update(resto['restaurant'])
        all_data.update({row : record})
        row += 1
    return pd.DataFrame.from_dict(all_data, orient='index')

def read_search_location_detail(json_data):
    all_data = dict()
    row = 0
    for resto in json_data:
        record = dict()
        record.update({'collection_id' : resto['restaurant']['collection_id']})
        record.update({'res_id' : resto['restaurant']['R']['res_id']})
        record.update(resto['restaurant']['location'])
        all_data.update({row : record})
        row += 1
    return pd.DataFrame.from_dict(all_data, orient='index')
        
def read_search_rating(json_data):
    all_data = dict()
    row = 0
    for item in json_data:
        record = dict()
        resto = copy.deepcopy(item)
        record.update({'collection_id' : resto['restaurant']['collection_id']})
        record.update({'res_id' : resto['restaurant']['R']['res_id']})
        del resto['restaurant']['user_rating']['rating_obj']
        resto['restaurant']['user_rating'].pop('custom_rating_text', None)
        resto['restaurant']['user_rating'].pop('custom_rating_text_background', None)
        resto['restaurant']['user_rating'].pop('rating_tool_tip', None)
        record.update(resto['restaurant']['user_rating'])
        all_data.update({row : record})
        row += 1
    return pd.DataFrame.from_dict(all_data, orient='index')

# Connect and Write to PostgreSQL

In [10]:
def connect_db():
    engine = create_engine(f"postgresql+psycopg2://{os.getenv('db-user')}:{os.getenv('db-pwd')}@{os.getenv('db-host')}",
                           client_encoding='utf-8')
    conn = engine.connect()
    return engine, conn

def close_db(engine, conn):
    conn.close()
    engine.dispose()
    
def save_to_db(data, table_name, if_exists='replace', dtype=None):
    engine, conn = connect_db()
    data.to_sql(table_name, conn, if_exists=if_exists, index=False, dtype=dtype)
    close_db(engine, conn)

# Fetching Data From PostgreSQL

In [11]:
def fetch_from_db(query):
    engine, conn = connect_db()
    result = conn.execute(query).fetchall()
    close_db(engine, conn)
    return pd.DataFrame(result, columns=result[0].keys())

# Data Request Main Function

In [22]:
HEADERS = headers = {'user-key' : os.getenv('user-key')}
list_cities = ['Jakarta', 'Bandung', 'Bali']

In [23]:
df_categories = read_categories(get_categories()[1])
df_cities = read_cities(get_cities(list_cities)[1])
df_collections = read_collections(get_collections(df_cities['id'])[1], df_cities['id'])

In [25]:
save_to_db(df_categories, 'categories', if_exists='replace')
save_to_db(df_cities, 'cities', if_exists='replace')
save_to_db(df_collections, 'collections', if_exists='replace')

In [26]:
list_city_id = df_cities['id']
list_collection_id = df_collections['collection_id'].unique()
status, raw_data = get_search(list_city_id, list_collection_id)

city_id:  11052 collection_id:  1
start:  0 results_found:  30 api call made:  1
city_id:  11052 collection_id:  1
start:  20 results_found:  30 api call made:  2
city_id:  11052 collection_id:  205557
start:  0 results_found:  16 api call made:  3
city_id:  11052 collection_id:  22
start:  0 results_found:  19 api call made:  4
city_id:  11052 collection_id:  291412
start:  0 results_found:  16 api call made:  5
city_id:  11052 collection_id:  3
start:  0 results_found:  15 api call made:  6
city_id:  11052 collection_id:  11
start:  0 results_found:  13 api call made:  7
city_id:  11052 collection_id:  205559
start:  0 results_found:  11 api call made:  8
city_id:  11052 collection_id:  20234
start:  0 results_found:  18 api call made:  9
city_id:  11052 collection_id:  12
start:  0 results_found:  43 api call made:  10
city_id:  11052 collection_id:  12
start:  20 results_found:  43 api call made:  11
city_id:  11052 collection_id:  12
start:  40 results_found:  43 api call made:  1

city_id:  170 collection_id:  321
start:  0 results_found:  0 api call made:  100
city_id:  170 collection_id:  52
start:  0 results_found:  0 api call made:  101
city_id:  170 collection_id:  248
start:  0 results_found:  0 api call made:  102
city_id:  170 collection_id:  536
start:  0 results_found:  0 api call made:  103
city_id:  170 collection_id:  30
start:  0 results_found:  0 api call made:  104
city_id:  170 collection_id:  25
start:  0 results_found:  0 api call made:  105
city_id:  170 collection_id:  65
start:  0 results_found:  0 api call made:  106
city_id:  170 collection_id:  2
start:  0 results_found:  0 api call made:  107
city_id:  170 collection_id:  310
start:  0 results_found:  0 api call made:  108
city_id:  170 collection_id:  249
start:  0 results_found:  0 api call made:  109
city_id:  170 collection_id:  303026
start:  0 results_found:  0 api call made:  110
city_id:  74 collection_id:  1
start:  0 results_found:  30 api call made:  111
city_id:  74 collecti

city_id:  74 collection_id:  35
start:  60 results_found:  67 api call made:  199
city_id:  74 collection_id:  5
start:  0 results_found:  32 api call made:  200
city_id:  74 collection_id:  5
start:  20 results_found:  32 api call made:  201
city_id:  74 collection_id:  675
start:  0 results_found:  75 api call made:  202
city_id:  74 collection_id:  675
start:  20 results_found:  75 api call made:  203
city_id:  74 collection_id:  675
start:  40 results_found:  75 api call made:  204
city_id:  74 collection_id:  675
start:  60 results_found:  75 api call made:  205
city_id:  74 collection_id:  321
start:  0 results_found:  47 api call made:  206
city_id:  74 collection_id:  321
start:  20 results_found:  47 api call made:  207
city_id:  74 collection_id:  321
start:  40 results_found:  47 api call made:  208
city_id:  74 collection_id:  52
start:  0 results_found:  44 api call made:  209
city_id:  74 collection_id:  52
start:  20 results_found:  44 api call made:  210
city_id:  74 co

In [27]:
df_location = read_search_location_detail(raw_data)
df_rating = read_search_rating(raw_data)
df_restaurant = read_search_restaurant_detail(raw_data)

In [28]:
display(df_location.shape)
display(df_rating.shape)
display(df_restaurant.shape)

(2060, 11)

(2060, 6)

(2060, 43)

In [29]:
save_to_db(df_location, 'locations', if_exists='replace')
save_to_db(df_rating, 'ratings', if_exists='replace')
save_to_db(df_restaurant, 'restaurants', if_exists='replace', dtype={'zomato_events':types.JSON})

# Get Latitude and Longitude For City

In [18]:
def center_city(city_address):
    geolocator = Nominatim(user_agent='id_explorer')
    location = geolocator.geocode(city_address)
    return location.latitude, location.longitude

# Restaurant Mapping in Folium

In [12]:
query = '''
WITH city_location AS (
    SELECT l.res_id, l.latitude, l.longitude, c.name, l.collection_id
    FROM locations AS l
    LEFT JOIN cities AS c
    ON l.city_id = c.id
)

SELECT l.latitude, l.longitude, l.name AS city_name, c.title, r.*, rt.aggregate_rating
FROM restaurants AS r
LEFT JOIN collections AS c
USING (collection_id)
LEFT JOIN city_location AS l
USING (res_id)
LEFT JOIN ratings AS rt
USING (res_id);
'''

In [14]:
clean_data = fetch_from_db(query).drop_duplicates(['collection_id', 'res_id'], ignore_index=True)
clean_data.head()

latitude       longitude city_name               title  collection_id  \
0  -6.9267573464  107.6171441004   Bandung  Trending This Week              1   
1  -6.8947930328  107.6054577157   Bandung  Trending This Week              1   
2  -6.9032710000  107.6323890000   Bandung  Trending This Week              1   
3  -6.8907515327  107.5961752608   Bandung  Trending This Week              1   
4  -6.8844210000  107.5966390000   Bandung  Trending This Week              1   

     res_id  is_grocery_store  delivery  takeway  \
0  18401633             False        -1       -1   
1  18401889             False        -1       -1   
2  18400544             False        -1       -1   
3  18389188             False        -1       -1   
4  18902158             False        -1       -1   

                             apikey  ... is_table_reservation_supported  \
0  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
1  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
2  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
3  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
4  d050ddf5d541dc1c00bee243f77554f3  ...                              0   

  has_table_booking                                         events_url  \
0                 0  https://www.zomato.com/bandung/rumah-lezat-sim...   
1                 0  https://www.zomato.com/bandung/yoshinoya-ciham...   
2                 0  https://www.zomato.com/bandung/sambel-hejo-nat...   
3                 0  https://www.zomato.com/bandung/ta-wan-sukajadi...   
4                 0  https://www.zomato.com/bandung/spice-affair-ba...   

                  phone_numbers      establishment establishment_types  \
0  Not available for this place    {"Quick Bites"}                None   
1                  022 82021790    {"Quick Bites"}                None   
2                   022 7233276    {"Quick Bites"}                None   
3                  022 82063590  {"Casual Dining"}                None   
4                  022 64401234  {"Casual Dining"}                None   

   medio_provider  book_url zomato_events aggregate_rating  
0            None      None          None              3.9  
1            None      None          None              3.8  
2            None      None          None              3.6  
3            None      None          None              3.9  
4            None      None          None              3.6  

[5 rows x 48 columns]

In [15]:
colormap = cm.LinearColormap(colors=['#D00000','#FFFF3F','#007F5F'], index=[0,2.5,5],vmin=0,vmax=5, caption='User Rating')
colormap

In [16]:
resto_Jakarta = clean_data[clean_data['city_name'] == 'Jakarta']
resto_Bandung = clean_data[clean_data['city_name'] == 'Bandung']
resto_Bali = clean_data[clean_data['city_name'] == 'Bali']

display(resto_Jakarta.shape)
display(resto_Bandung.shape)
display(resto_Bali.shape)

(1547, 48)

(233, 48)

(190, 48)

In [17]:
resto_Jakarta.head()

latitude       longitude city_name               title  \
337  -6.2323250000  106.8187280000   Jakarta     All you can eat   
403  -6.1657670000  106.8197010000   Jakarta   Legendary Outlets   
421  -6.1551070000  106.8176380000   Jakarta  Trending This Week   
426  -6.1409790000  106.8541120000   Jakarta  Trending This Week   
427  -6.2411560000  106.6284430000   Jakarta  Trending This Week   

     collection_id    res_id  is_grocery_store  delivery  takeway  \
337            537  19258573             False        -1       -1   
403              7   7405302             False        -1       -1   
421              1   7405742             False        -1       -1   
426              1   7421970             False        -1       -1   
427              1  19113274             False        -1       -1   

                               apikey  ... is_table_reservation_supported  \
337  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
403  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
421  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
426  d050ddf5d541dc1c00bee243f77554f3  ...                              0   
427  d050ddf5d541dc1c00bee243f77554f3  ...                              0   

    has_table_booking                                         events_url  \
337                 0  https://www.zomato.com/jakarta/shabu-hachi-gat...   
403                 0  https://www.zomato.com/jakarta/ragusa-es-itali...   
421                 0  https://www.zomato.com/jakarta/bakmi-gm-1-gaja...   
426                 0  https://www.zomato.com/jakarta/botany-all-day-...   
427                 0  https://www.zomato.com/jakarta/happy-lemon-ser...   

     phone_numbers        establishment establishment_types  medio_provider  \
337  0811 97116701    {"Casual Dining"}                  {}            None   
403    021 3849123  {"Dessert Parlour"}                  {}            None   
421   021 63862229      {"Quick Bites"}                None            None   
426   021 29568800    {"Casual Dining"}                None            None   
427    021 5470955    {"Beverage Shop"}                None            None   

     book_url zomato_events aggregate_rating  
337      None          None              4.4  
403      None          None              3.3  
421      None          None              4.1  
426      None          None              3.7  
427      None          None              3.6  

[5 rows x 48 columns]

In [35]:
def map_generator(city_address, resto_df, zoom_start=11):
    Map = folium.Map(location=center_city(city_address), zoom_start=zoom_start, tiles='CartoDB positron')

    for idx, row in resto_df.iterrows():
        html = f'''
        <p style="font-family:georgia,garamond,serif;">
            <span style="font-size:25px;color:#D00000;"><i><b>{row['name']}</b></i></span>
            <br><br>
            <img height=150px align="right" src={row['thumb']}>
            <br>
            <span style="font-size:16px;">Collection:<br><b>{row['title']}</b></span>
            <br><br>
            <span style="font-size:16px;">Rating:<br><b>{row['aggregate_rating']}</b></span>
        </p>
        '''
        iframe = folium.IFrame(html)
        popup = folium.Popup(iframe, min_width=400, max_width=700, min_height=400, max_height=700)
        folium.CircleMarker(location=[row['latitude'], row['longitude']], tooltip=row['name'],
                            radius=5, 
                            color=None,
                            fill_color=colormap(float(row['aggregate_rating'])), fill_opacity=0.5,
                            popup=popup
                           ).add_to(Map)

    colormap.add_to(Map)
    Map.save(f'{city_address} map.html')
    return Map

### Resto Map - Jakarta, colored by User's Rating

In [33]:
map_generator('Jakarta, ID', resto_Jakarta)

### Resto Map - Bandung, colored by User's Rating

In [36]:
map_generator('Bandung, ID', resto_Bandung, zoom_start=12)

### Resto Map - Bali, colored by User's Rating

In [38]:
map_generator('Denpasar, ID', resto_Bali)

# Project Showcase Using Streamlit

# Publish Project Using Heroku